**0. Preliminary Works:** how big is the file,number of lines, etc.<br>
**1. Prepare sample file:** create small file to work with.<br>
**2. Study the Data**<br>
**3. Select Columns of Interest**<br>
**4. Data Cleaning**<br>
    4.1. What to do with NaN<br>
    4.2. Make an action plan<br>
**5. Visualization**<br>
**6. Modelling**<br>
**7. Evaluation**<br>
**FINAL: Adjust the code to work with Big data**<br>
    5.1. Create an ITERATOR from the data base and define CHUNK size <br>
    5.2. Test Big Data approach on a sample

# 0. Premilinary Works
How big is the file, number of rows, etc.

In [1]:
!ls -Rl
# 2019_Yellow_Taxi_Trip_Data.csv is 4.243.651.749  bytes (7,63 GB)

.:
total 7376
-rw-rw-rw- 1 angelrps angelrps  143136 Apr  2 16:55  04-group_by_inclass.ipynb
drwxrwxrwx 1 angelrps angelrps     512 Apr  1 18:31  Data
-rwxrwxrwx 1 angelrps angelrps 3851713 Apr  6 10:42  Data_Analysis.ipynb
-rw-rw-rw- 1 angelrps angelrps   10144 Apr  1 12:33  HowToTackleDataScienceChallenge.ipynb
-rw-rw-rw- 1 angelrps angelrps      12 Apr  2 19:48  README.md
---------- 1 angelrps angelrps    9058 Apr  1 19:59  Schedule.xlsx
-rwxrwxrwx 1 angelrps angelrps 3527394 Apr  2 17:37  TSA.ipynb
---------- 1 angelrps angelrps     165 Apr  6 09:21 '~$Schedule.xlsx'

./Data:
total 18975828
-rwxrwxrwx 1 angelrps angelrps 10532305815 Mar 25 13:15  2017_Yellow_Taxi_Trip_Data.csv
-rwxrwxrwx 1 angelrps angelrps  8197837930 Apr  2 18:02  2019_Yellow_Taxi_Trip_Data.csv
-rwxrwxrwx 1 angelrps angelrps       75537 Apr  4 12:49  data_dictionary_trip_records_green.pdf
-rwxrwxrwx 1 angelrps angelrps      196848 Apr  4 12:39  data_dictionary_trip_records_yellow.pdf
-rwxrwxrwx 1 angelrps angelrp

In [2]:
# count lines
!wc -l ./Data/2019_Yellow_Taxi_Trip_Data.csv
# the file has 43.801.887 lines

84399020 ./Data/2019_Yellow_Taxi_Trip_Data.csv


In [3]:
!head -5 ./Data/2019_Yellow_Taxi_Trip_Data.csv
# There is a header
# And the separator is ','
# Columns 'tpep_pickup_datetime' and 'tpep_dropoff_datetime' should be imported as datetime

VendorID,tpep_pickup_datetime,tpep_dropoff_datetime,passenger_count,trip_distance,RatecodeID,store_and_fwd_flag,PULocationID,DOLocationID,payment_type,fare_amount,extra,mta_tax,tip_amount,tolls_amount,improvement_surcharge,total_amount,congestion_surcharge
1,04/29/2019 11:31:03 AM,04/29/2019 11:31:03 AM,1,0,1,N,231,264,2,2.5,2.5,0.5,0,0,0.3,5.8,2.5
2,04/29/2019 10:52:08 AM,04/29/2019 11:06:18 AM,1,1.01,1,N,186,230,1,10,0,0.5,2.66,0,0.3,15.96,2.5
2,04/29/2019 11:28:40 AM,04/29/2019 11:33:01 AM,1,0.82,1,N,238,151,1,5,0,0.5,1.66,0,0.3,9.96,2.5
1,04/29/2019 11:28:06 AM,04/29/2019 12:07:32 PM,1,12.1,1,N,138,88,1,38.5,2.5,0.5,10.4,0,0.3,52.2,2.5


# 1. Prepare sample file
I will take ~ 5.000 for the sample file out of the 84 million lines of the file

In [4]:
import pandas as pd
import random
pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [5]:
# TAKING RANDOM SAMPLE OF ~5.000 ROWS
# I will also parse the datetime columns to the right object type
p = 0.0001 # take 0.01 percent of total rows
dsample = pd.read_csv('./Data/2019_Yellow_Taxi_Trip_Data.csv',sep=',',header=0,
                parse_dates = {'pickup_datetime':['tpep_pickup_datetime'],'dropoff_datetime':['tpep_dropoff_datetime']},
                skiprows=lambda i: i>0 and random.random() > p)

In [6]:
dsample.shape

(8327, 18)

In [7]:
# CREATE SAMPLE DATASET WITH 100 LINES WITH BASH

# it may or it may not have header
#!shuf -n 100 ./Data/2017_Yellow_Taxi_Trip_Data.csv > ./Data/sample100.csv

# without header
#!tail -n +2 ./Data/2017_Yellow_Taxi_Trip_Data.csv | shuf -n 100 > ./Data/sample100.csv

# 2. Study the Data
```python
b.shape         #check nº of rows and columns
list(b.columns) #check white spaces in column names
b.sample()      #check random sample
                #ask for the data dictionary and study all fields
b.info()        #check data types and spot nulls
b.describe()    #check descriptive statistics
```

In [8]:
dsample.shape, list(dsample.columns)
# I get the expected number of rows
# Column names have no spaces

((8327, 18),
 ['pickup_datetime',
  'dropoff_datetime',
  'VendorID',
  'passenger_count',
  'trip_distance',
  'RatecodeID',
  'store_and_fwd_flag',
  'PULocationID',
  'DOLocationID',
  'payment_type',
  'fare_amount',
  'extra',
  'mta_tax',
  'tip_amount',
  'tolls_amount',
  'improvement_surcharge',
  'total_amount',
  'congestion_surcharge'])

In [9]:
dsample.sample(5)
# I have checked the data dictionary "data_dictionary_trip_records_yellow.pdf"
# values on this sample seem to make sense

pickup_datetime    dropoff_datetime  VendorID  passenger_count  \
906  2019-06-05 20:03:49 2019-06-05 20:10:13       1.0              1.0   
5073 2019-12-15 05:19:31 2019-12-15 05:49:15       2.0              2.0   
2319 2019-08-11 17:42:22 2019-08-11 18:00:11       2.0              2.0   
5513 2019-01-06 18:41:20 2019-01-06 19:18:52       1.0              0.0   
233  2019-05-09 06:17:56 2019-05-09 06:25:56       1.0              1.0   

      trip_distance  RatecodeID store_and_fwd_flag  PULocationID  \
906            1.20         1.0                  N           166   
5073          10.33         1.0                  N           100   
2319           2.56         1.0                  N            68   
5513           6.20         1.0                  N            68   
233            5.50         1.0                  N           132   

      DOLocationID  payment_type  fare_amount  extra  mta_tax  tip_amount  \
906             41           1.0          6.5    0.5      0.5        1.00   
5073            61           1.0         32.0    0.5      0.5        8.38   
2319           114           1.0         13.0    0.0      0.5        2.44   
5513           181           1.0         25.0    0.0      0.5        6.45   
233            139           2.0         16.0    0.0      0.5        0.00   

      tolls_amount  improvement_surcharge  total_amount  congestion_surcharge  
906           0.00                    0.3          8.80                   0.0  
5073          6.12                    0.3         50.30                   2.5  
2319          0.00                    0.3         18.74                   2.5  
5513          0.00                    0.3         32.25                   NaN  
233           0.00                    0.3         16.80                   0.0

In [10]:
dsample.info()
# there are no null values
# data types seem correct

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8327 entries, 0 to 8326
Data columns (total 18 columns):
pickup_datetime          8327 non-null datetime64[ns]
dropoff_datetime         8327 non-null datetime64[ns]
VendorID                 8295 non-null float64
passenger_count          8295 non-null float64
trip_distance            8327 non-null float64
RatecodeID               8295 non-null float64
store_and_fwd_flag       8295 non-null object
PULocationID             8327 non-null int64
DOLocationID             8327 non-null int64
payment_type             8295 non-null float64
fare_amount              8327 non-null float64
extra                    8327 non-null float64
mta_tax                  8327 non-null float64
tip_amount               8327 non-null float64
tolls_amount             8327 non-null float64
improvement_surcharge    8327 non-null float64
total_amount             8327 non-null float64
congestion_surcharge     7847 non-null float64
dtypes: datetime64[ns](2), float64(13)

In [11]:
dsample.describe()
# I see that:
# There are trips with 0 'trip_distance'
# There are trips with negative 'fare_amount'

VendorID  passenger_count  trip_distance   RatecodeID  PULocationID  \
count  8295.000000      8295.000000    8327.000000  8295.000000   8327.000000   
mean      1.643641         1.550090       2.916945     1.051115    163.413234   
std       0.500374         1.186845       3.724918     0.353822     66.158988   
min       1.000000         0.000000      -2.400000     1.000000      4.000000   
25%       1.000000         1.000000       0.960000     1.000000    116.000000   
50%       2.000000         1.000000       1.600000     1.000000    162.000000   
75%       2.000000         2.000000       3.010000     1.000000    233.000000   
max       4.000000         6.000000      38.180000     5.000000    265.000000   

       DOLocationID  payment_type  fare_amount        extra      mta_tax  \
count   8327.000000   8295.000000  8327.000000  8327.000000  8327.000000   
mean     162.072535      1.291621    13.005563     1.077801     0.495437   
std       70.896675      0.479325    11.532020     1.237590     0.056763   
min        1.000000      1.000000   -12.000000    -1.000000    -0.500000   
25%      107.000000      1.000000     6.500000     0.000000     0.500000   
50%      162.000000      1.000000     9.500000     0.500000     0.500000   
75%      234.000000      2.000000    14.500000     2.500000     0.500000   
max      265.000000      4.000000   240.000000     7.000000     0.500000   

        tip_amount  tolls_amount  improvement_surcharge  total_amount  \
count  8327.000000   8327.000000            8327.000000   8327.000000   
mean      2.115948      0.355313               0.298775     18.675214   
std       2.546869      1.533730               0.026682     14.126021   
min       0.000000     -6.120000              -0.300000    -21.920000   
25%       0.000000      0.000000               0.300000     11.025000   
50%       1.850000      0.000000               0.300000     14.300000   
75%       2.860000      0.000000               0.300000     20.380000   
max      35.000000     21.000000               0.300000    246.920000   

       congestion_surcharge  
count           7847.000000  
mean               2.189372  
std                0.838136  
min               -2.500000  
25%                2.500000  
50%                2.500000  
75%                2.500000  
max                2.500000

#### Check trip_distance = 0
**CONCLUSION:**<br>
I will remove all trips with 'trip_distance' < 0.06 (100 meters) because I consider them either measurement errors or non representative data.

In [12]:
dsample['ZeroDistCount'] = 1
dsample.groupby('trip_distance', as_index = False)['ZeroDistCount'].sum()
# there are 46 rows in this sample with 0 distance and few others with distances under 100 meters (0.06 miles)

trip_distance  ZeroDistCount
0             -2.40              1
1              0.00             66
2              0.01              3
3              0.02              3
4              0.03              1
5              0.04              2
6              0.05              3
7              0.07              2
8              0.08              1
9              0.09              1
10             0.10              7
11             0.11              1
12             0.13              1
13             0.14              4
14             0.17              2
15             0.18              2
16             0.19              1
17             0.20             12
18             0.21              3
19             0.22              2
20             0.23              2
21             0.24              2
22             0.25              1
23             0.26              2
24             0.28              3
25             0.29              5
26             0.30             47
27             0.31              5
28             0.32              3
29             0.33              5
30             0.34              4
31             0.35              7
32             0.36              8
33             0.37             13
34             0.38              7
35             0.39             16
36             0.40             72
37             0.41              7
38             0.42             18
39             0.43              7
40             0.44             15
41             0.45             11
42             0.46             12
43             0.47              8
44             0.48              9
45             0.49             11
46             0.50            101
47             0.51             13
48             0.52             21
49             0.53             19
50             0.54             18
51             0.55             15
52             0.56             20
53             0.57             13
54             0.58             19
55             0.59             20
56             0.60            140
57             0.61             20
58             0.62             22
59             0.63             14
60             0.64             19
61             0.65             19
62             0.66             23
63             0.67             20
64             0.68             28
65             0.69             16
66             0.70            175
67             0.71             25
68             0.72             25
69             0.73             21
70             0.74             17
71             0.75             20
72             0.76             23
73             0.77             24
74             0.78             30
75             0.79             31
76             0.80            160
77             0.81             28
78             0.82             24
79             0.83             33
80             0.84             25
81             0.85             22
82             0.86             22
83             0.87             20
84             0.88             37
85             0.89             26
86             0.90            154
87             0.91             25
88             0.92             16
89             0.93             20
90             0.94             24
91             0.95             33
92             0.96             25
93             0.97             19
94             0.98             20
95             0.99             21
96             1.00            167
97             1.01             28
98             1.02             23
99             1.03             26
100            1.04             26
101            1.05             23
102            1.06             19
103            1.07             23
104            1.08             21
105            1.09             16
106            1.10            172
107            1.11             19
108            1.12             19
109            1.13             22
110            1.14             17
111            1.15             12
112            1.16             20
113            1

#### Check negative fare_amount values
CONCLUSION:<br>
There are 6 rows with negative fare_amount and one row with 0.01. I will remove these rows which fare amount is less that 1$ because I consider them measurement errors.

In [13]:
dsample['FareCount'] = 1
dsample[dsample['fare_amount']<1].groupby('fare_amount', as_index = False)['FareCount'].sum()
# There are 12 rows in this sample with negative fare_amount and one row with 0.01.

fare_amount  FareCount
0        -12.00          1
1        -11.00          1
2         -8.50          1
3         -7.50          1
4         -6.50          1
5         -5.00          2
6         -4.50          3
7         -4.00          1
8         -3.50          1
9         -3.00          2
10        -2.50          2
11         0.00          3
12         0.01          2

In [14]:
# Groupby DATE and sort values to check if all the data is from 2019
dsample['DayCount'] = 1
d = dsample[['pickup_datetime', 'DayCount']].groupby([dsample['pickup_datetime'].dt.date]).sum().reset_index().sort_values('pickup_datetime')
d.head(), d.tail()
# I verify that all data belongs to the same year
# Also verify that there is data from January to December

(  pickup_datetime  DayCount
 0      2019-01-01        14
 1      2019-01-02        19
 2      2019-01-03        14
 3      2019-01-04        20
 4      2019-01-05        19,     pickup_datetime  DayCount
 360      2019-12-27        15
 361      2019-12-28        11
 362      2019-12-29        18
 363      2019-12-30        24
 364      2019-12-31        16)

# 3. Select Columns of Interest
```python
'pickup_datetime':  # The date and time when the meter was engage
'dropoff_datetime': # The date and time when the meter was disengage
'trip_distance':    # The elapsed trip distance in miles reported by the taximeter
'PULocationID':     # TLC Taxi Zone in which the taximeter was engaged
'DOLocationID':     # TLC Taxi Zone in which the taximeter was disengaged
'fare_amount':      # The time-and-distance fare calculated by the meter
```

In [15]:
dsample2 = dsample[['pickup_datetime', 'dropoff_datetime', 'trip_distance', 'PULocationID', 'DOLocationID', 'fare_amount']]
dsample2

pickup_datetime    dropoff_datetime  trip_distance  PULocationID  \
0    2019-04-29 12:33:39 2019-04-29 12:38:35           1.40           151   
1    2019-04-29 13:22:35 2019-04-29 13:41:51           2.67           151   
2    2019-04-29 13:23:11 2019-04-29 13:30:10           0.75           161   
3    2019-04-29 14:50:53 2019-04-29 15:37:24          15.29            10   
4    2019-04-29 14:38:47 2019-04-29 14:47:23           1.70           170   
5    2019-04-29 16:06:18 2019-04-29 16:17:55           2.20           236   
6    2019-04-29 16:19:22 2019-04-29 16:20:08           0.00           141   
7    2019-04-29 18:36:43 2019-04-29 18:41:34           0.60           229   
8    2019-04-29 18:20:56 2019-04-29 18:40:31           1.90           229   
9    2019-04-29 18:02:46 2019-04-29 18:08:33           1.10           161   
10   2019-04-29 19:31:45 2019-04-29 19:47:13           2.10           238   
11   2019-04-29 20:31:00 2019-04-29 20:35:01           0.60           162   
12   2019-04-29 21:23:29 2019-04-29 21:51:57           7.59           239   
13   2019-04-29 21:37:55 2019-04-29 21:44:44           1.53            48   
14   2019-04-29 22:03:00 2019-04-29 22:19:57           3.80           230   
15   2019-04-29 23:36:00 2019-04-29 23:45:57           1.40           233   
16   2019-04-30 00:24:07 2019-04-30 00:32:38           1.30           164   
17   2019-04-30 05:18:50 2019-04-30 05:36:36          10.16           107   
18   2019-04-30 05:24:47 2019-04-30 05:33:50           1.80           140   
19   2019-04-30 07:31:07 2019-04-30 07:44:38           5.40           229   
20   2019-04-30 07:59:09 2019-04-30 08:08:27           1.88           140   
21   2019-04-30 09:45:01 2019-04-30 09:50:51           0.72           141   
22   2019-04-30 09:51:26 2019-04-30 10:03:19           1.20            90   
23   2019-04-30 09:19:07 2019-04-30 09:31:52           2.20            75   
24   2019-04-30 10:41:51 2019-04-30 10:45:14           0.30           237   
25   2019-04-30 10:35:08 2019-04-30 11:05:36           3.17           186   
26   2019-04-30 11:13:50 2019-04-30 11:37:04           5.74           261   
27   2019-04-30 12:02:06 2019-04-30 12:13:39           0.62           162   
28   2019-04-30 12:05:34 2019-04-30 12:22:50           1.23           229   
29   2019-04-30 12:03:37 2019-04-30 12:39:35           7.49           263   
30   2019-04-30 13:12:47 2019-04-30 13:38:17           9.15           138   
31   2019-04-30 15:52:04 2019-04-30 16:36:32          11.30           138   
32   2019-04-30 15:29:40 2019-04-30 15:40:46           1.50            68   
33   2019-04-30 15:07:45 2019-04-30 15:23:09           1.62           234   
34   2019-04-30 17:58:19 2019-04-30 18:02:14           0.70           186   
35   2019-04-30 17:25:43 2019-04-30 17:37:49           1.90           164   
36   2019-04-30 18:33:03 2019-04-30 18:38:37           0.94           166   
37   2019-04-30 18:04:58 2019-04-30 18:20:19           1.41           163   
38   2019-04-30 20:59:33 2019-04-30 21:15:16           3.30           236   
39   2019-04-30 20:07:22 2019-04-30 20:23:55           3.00           236   
40   2019-04-30 21:44:38 2019-04-30 21:58:30           2.30           186   
41   2019-04-30 21:43:26 2019-04-30 21:50:58           1.40           238   
42   2019-04-30 21:49:08 2019-04-30 21:52:23           0.69           162   
43   2019-04-30 22:53:59 2019-04-30 23:08:51           4.93           107   
44   2019-04-30 23:57:43 2019-05-01 00:05:13           1.50           161   
45   2019-04-30 23:28:22 2019-04-30 23:40:57           2.54            90   
46   2019-05-01 01:51:12 2019-05-01 02:06:19           3.94           144   
47   2019-05-01 02:29:29 2019-05-01 02:55:55           6.33           113   
48   2019-05-01 09:09:43 2019-05-01 09:26:01           2.01           170   
49   2019-05-01 09:05:35 2019-05-01 09:16:37           0.80           163   
50   2019-05-01 10:33:36 2019-05-01 10:36:27           0.76           239   
51   

# 4. Data Cleaning
- REMOVE 'trip_distance' < 0.06 miles (100m) <br>
- REMOVE 'fare_amount' < 1$ <br>

In [26]:
# REMOVE 'trip_distance' < 0.06 AND 'fare_amount' < 1
dsample2 = dsample2[(dsample['trip_distance']>0.06) & (dsample['fare_amount']>=1)]
dsample2

/home/angelrps/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


pickup_datetime    dropoff_datetime  trip_distance  PULocationID  \
0    2019-04-29 12:33:39 2019-04-29 12:38:35           1.40           151   
1    2019-04-29 13:22:35 2019-04-29 13:41:51           2.67           151   
2    2019-04-29 13:23:11 2019-04-29 13:30:10           0.75           161   
3    2019-04-29 14:50:53 2019-04-29 15:37:24          15.29            10   
4    2019-04-29 14:38:47 2019-04-29 14:47:23           1.70           170   
5    2019-04-29 16:06:18 2019-04-29 16:17:55           2.20           236   
7    2019-04-29 18:36:43 2019-04-29 18:41:34           0.60           229   
8    2019-04-29 18:20:56 2019-04-29 18:40:31           1.90           229   
9    2019-04-29 18:02:46 2019-04-29 18:08:33           1.10           161   
10   2019-04-29 19:31:45 2019-04-29 19:47:13           2.10           238   
11   2019-04-29 20:31:00 2019-04-29 20:35:01           0.60           162   
12   2019-04-29 21:23:29 2019-04-29 21:51:57           7.59           239   
13   2019-04-29 21:37:55 2019-04-29 21:44:44           1.53            48   
14   2019-04-29 22:03:00 2019-04-29 22:19:57           3.80           230   
15   2019-04-29 23:36:00 2019-04-29 23:45:57           1.40           233   
16   2019-04-30 00:24:07 2019-04-30 00:32:38           1.30           164   
17   2019-04-30 05:18:50 2019-04-30 05:36:36          10.16           107   
18   2019-04-30 05:24:47 2019-04-30 05:33:50           1.80           140   
19   2019-04-30 07:31:07 2019-04-30 07:44:38           5.40           229   
20   2019-04-30 07:59:09 2019-04-30 08:08:27           1.88           140   
21   2019-04-30 09:45:01 2019-04-30 09:50:51           0.72           141   
22   2019-04-30 09:51:26 2019-04-30 10:03:19           1.20            90   
23   2019-04-30 09:19:07 2019-04-30 09:31:52           2.20            75   
24   2019-04-30 10:41:51 2019-04-30 10:45:14           0.30           237   
25   2019-04-30 10:35:08 2019-04-30 11:05:36           3.17           186   
26   2019-04-30 11:13:50 2019-04-30 11:37:04           5.74           261   
27   2019-04-30 12:02:06 2019-04-30 12:13:39           0.62           162   
28   2019-04-30 12:05:34 2019-04-30 12:22:50           1.23           229   
29   2019-04-30 12:03:37 2019-04-30 12:39:35           7.49           263   
30   2019-04-30 13:12:47 2019-04-30 13:38:17           9.15           138   
31   2019-04-30 15:52:04 2019-04-30 16:36:32          11.30           138   
32   2019-04-30 15:29:40 2019-04-30 15:40:46           1.50            68   
33   2019-04-30 15:07:45 2019-04-30 15:23:09           1.62           234   
34   2019-04-30 17:58:19 2019-04-30 18:02:14           0.70           186   
35   2019-04-30 17:25:43 2019-04-30 17:37:49           1.90           164   
36   2019-04-30 18:33:03 2019-04-30 18:38:37           0.94           166   
37   2019-04-30 18:04:58 2019-04-30 18:20:19           1.41           163   
38   2019-04-30 20:59:33 2019-04-30 21:15:16           3.30           236   
39   2019-04-30 20:07:22 2019-04-30 20:23:55           3.00           236   
40   2019-04-30 21:44:38 2019-04-30 21:58:30           2.30           186   
41   2019-04-30 21:43:26 2019-04-30 21:50:58           1.40           238   
42   2019-04-30 21:49:08 2019-04-30 21:52:23           0.69           162   
43   2019-04-30 22:53:59 2019-04-30 23:08:51           4.93           107   
44   2019-04-30 23:57:43 2019-05-01 00:05:13           1.50           161   
45   2019-04-30 23:28:22 2019-04-30 23:40:57           2.54            90   
46   2019-05-01 01:51:12 2019-05-01 02:06:19           3.94           144   
47   2019-05-01 02:29:29 2019-05-01 02:55:55           6.33           113   
48   2019-05-01 09:09:43 2019-05-01 09:26:01           2.01           170   
49   2019-05-01 09:05:35 2019-05-01 09:16:37           0.80           163   
50   2019-05-01 10:33:36 2019-05-01 10:36:27           0.76           239   
51   2019-05-01 12:16:15 2019-05-01 12:43:30           7.86           244   
52   

In [31]:
# REMOVE 'trip_distance' < 0.06 AND 'fare_amount' < 1
dsample2[dsample2['trip_distance']<0.06]
# dsample2[dsample2['fare_amount']<1]

Empty DataFrame
Columns: [pickup_datetime, dropoff_datetime, trip_distance, PULocationID, DOLocationID, fare_amount]
Index: []